<font color = green >

# Text classification: topic modeling 

</font>

<font color = green >

### Latent Dirichlet allocation (LDA)

</font>

Typically used to detect underlying topics in the text documents

**Input** : text documents and number of topics 
<br>
**Output**: Distribution of topics for each document (that allows to assign th one with highest probability) and word distribution for each topic 

**Assumptions**:
- Documents with similar topics use similar groups of words 
- Documents are probability distribution over latent topics 
- Topics are probability distribution over words


<font color = green >

#### Generative process
<br>
</font>

LDA considers the every document is created the following way:

1) Define number if words in the document
<br>
2) Chose the topic mixture over the fixed set of topics (e.g. 20% of topic A, 30% of topic A, and 50% of topic A)
<br>
3) Generate the words by:
<br>
   -pick the topic based on document's multinomial distribution 
<br>
   -pick the word based on topic's multinomial distribution 

<img src = "img/topics_modeling.png" height=500 width= 800 align="left">



<font color = green >

#### Recall
</font>


#### Binomial distribution

$$p(k/n)\quad =\quad C^{ k }_{ n }\cdot p^{ k }(1-p)^{ n-k }\quad =\quad \frac { n! }{ k!(n-k)! } p^{ k }(1-p)^{ n-k }$$

Example: Probability of 6 of 10 for fear coin: 
$$p(6,4)\quad =\quad C^{ 6 }_{ 10 }\cdot {0.5}^{ 6 }(0.5)^{ 4 }\quad = 210 \cdot 0.015625 \cdot 0.0625 = 0.205078125$$


#### Multinomial distribution

$$p(n_{ 1 }n_{ 2 }...n_{ k })\quad =\quad \frac { n! }{ n_{ 1 }!n_{ 2 }!...n_{ k }! } p^{ n_{ 1 } }_{ 1 }p^{ n_{ 2 } }_{ 2 }...p^{ n_{ k } }_{ k }$$

Example (three outcomes): <br>
n = 12 (12 games are played),<br>
n1 = 7 (number won by Player A),<br>
n2 = 2 (number won by Player B),<br>
n3 = 3 (the number drawn),<br>
p1 = 0.4 (probability Player A wins)<br>
p2 = 0.35(probability Player B wins)<br>
p3 = 0.25(probability of a draw)<br>
$$p(7,2,3)\quad =\quad \frac {12!}{ 7! \cdot 2! \cdot3 ! }  \cdot 0.4^{7} \cdot 0.35^{2} \cdot0.25^{3} = 0.0248$$




<font color = green >

#### Maximul Likelihood Estimation

</font>

<br>

**Recall** 
<br> Known are text documents and number $K$ of topics 

**Target**:
<br>Within all possible topics distribution for all documemnts and all possible words distribution for topics, shoose the one wich maximizes probability of all text documents.

**Approach** :
<br>
1) Randomly assign each word of each document to $K$ topics 
<br>
2) Iterate the following process till convergence (steady assignments of w to topics) 
<br>$\quad\quad$For each document $d$: 
<br>
    $\quad\quad\bullet$ Assume that all topic assignment except current one are correct     
    $\quad\quad\bullet$ For each word $w$ in $d$:           
    $\quad\quad\quad$ - For every topic $t$ compare the the score for hypothesis that w is in this topic $t$:
   <br>$\quad\quad\quad\quad\quad score (t) =  p(t | d) \cdot p (w |t),$
   <br>$\quad\quad\quad\quad p(t|d)$ is proportion of all words in d from t,
    <br>$\quad\quad\quad\quad p(w|t)$ is share of word w in topic t.  
    $\quad\quad\quad$ - Assign the word w to the topic with max score
    <br>$\quad\quad\bullet$ Iterate through all $w$ in $d$:           
$\quad\quad$Iterate through all $d$

Te results is matrix of distribution of words in topics  
Note: The computed topics are just words distribution, i.e. need to summarize them somehow. 


<font color = green >

## Gensim LDA 

</font>



In [1]:
from nltk.tokenize import word_tokenize
from nltk.stem.porter import PorterStemmer
from gensim import corpora, models
import gensim
from nltk.corpus import stopwords

<font color = green >

### Define the text documents 

</font>



In [2]:
doc_a = "Brocolli is good to eat. My brother likes to eat good brocolli, but not my mother."
doc_b = "My mother spends a lot of time driving my brother around to baseball practice."
doc_c = "Some health experts suggest that driving may cause increased tension and blood pressure."
doc_d = "I often feel pressure to perform well at school, but my mother never seems to drive my brother to do better."
doc_e = "Health professionals say that brocolli is good for your health."
doc_set = [doc_a, doc_b, doc_c, doc_d, doc_e]


<font color = green >

### Tokenize, clean, and stem

</font>



In [3]:
en_stop  = set(stopwords.words('english'))
p_stemmer = PorterStemmer()

def tokenize(doc_set):
    texts = []
    for doc in doc_set:
        # tokenize document string
        raw = doc.lower()
        tokens = word_tokenize(raw)

        # remove stop words from tokens
        tokens = [token for token in tokens if token not in en_stop]

        # stem tokens
        tokens = [p_stemmer.stem(token) for token in tokens]

        # add tokens to list
        texts.append(tokens)
    return texts

texts = tokenize(doc_set)
texts[0]

['brocolli',
 'good',
 'eat',
 '.',
 'brother',
 'like',
 'eat',
 'good',
 'brocolli',
 ',',
 'mother',
 '.']

<font color = green >

### Convert tokenized documents into a "id <-> term" dictionary

</font>



In [4]:
dictionary = corpora.Dictionary(texts) # this is alternative way - without using count vectorizer
print (type(dictionary), dictionary)
for k,w in dictionary.items():
    print (k,w)

<class 'gensim.corpora.dictionary.Dictionary'> Dictionary(34 unique tokens: [',', '.', 'brocolli', 'brother', 'eat']...)
0 ,
1 .
2 brocolli
3 brother
4 eat
5 good
6 like
7 mother
8 around
9 basebal
10 drive
11 lot
12 practic
13 spend
14 time
15 blood
16 caus
17 expert
18 health
19 increas
20 may
21 pressur
22 suggest
23 tension
24 better
25 feel
26 never
27 often
28 perform
29 school
30 seem
31 well
32 profession
33 say


<font color = green >

### Create gensim corpus

</font>



In [5]:
print ('\nconvert tokenized documents into a document-term matrix')
corpus = [dictionary.doc2bow(text) for text in texts] # id and count
for item in corpus:
    print (item)


convert tokenized documents into a document-term matrix
[(0, 1), (1, 2), (2, 2), (3, 1), (4, 2), (5, 2), (6, 1), (7, 1)]
[(1, 1), (3, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1)]
[(1, 1), (10, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1)]
[(0, 1), (1, 1), (3, 1), (7, 1), (10, 1), (21, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1)]
[(1, 1), (2, 1), (5, 1), (18, 2), (32, 1), (33, 1)]


<font color = green >

### Generate LDA model

</font>



In [6]:
ldamodel = gensim.models.ldamodel.LdaModel(
    corpus, num_topics=2, id2word=dictionary, passes=20, random_state= 0)


<font color = green >

### Review topics 

</font>



In [7]:
ldamodel.print_topics(num_topics=2,num_words=10)

[(0,
  '0.098*"." + 0.076*"brocolli" + 0.076*"good" + 0.055*"mother" + 0.055*"brother" + 0.054*"health" + 0.054*"eat" + 0.033*"," + 0.033*"like" + 0.033*"spend"'),
 (1,
  '0.060*"drive" + 0.059*"pressur" + 0.059*"." + 0.036*"," + 0.036*"never" + 0.036*"often" + 0.036*"increas" + 0.036*"perform" + 0.036*"seem" + 0.036*"well"')]

<font color = green >

### Classify the new text 

</font>



In [8]:
test_doc_list = ["Some experts suggest that car may cause increased blood pressure. professionals say that brocolli is good "]
test_texts = tokenize(test_doc_list)
test_corpus = [dictionary.doc2bow(text) for text in test_texts ]
test_doc_topics = ldamodel.get_document_topics(test_corpus)
print ('\nget topics:')
for el in test_doc_topics: # loop over all tests in provided list
    print(el)


get topics:
[(0, 0.37417653), (1, 0.62582344)]


<font color = green >

### Sample of topic modeling on large dataset

</font>



In [9]:
from sklearn.feature_extraction.text import CountVectorizer
import pickle

<font color = green >

#### Load "News" data 

</font>



In [10]:
import os
cwd= os.getcwd()
path = os.path.join(cwd,)
fn=  os.path.join(path , 'newsgroups')

with open(fn, 'rb') as f:
    newsgroup_data = pickle.load(f)

<font color = green >

#### Review data

</font>



In [11]:
print (type(newsgroup_data))
print ('len of documents = {:,}\n'.format(len(newsgroup_data)))

newsgroup_data[0]

<class 'list'>
len of documents = 2,000



"The best group to keep you informed is the Crohn's and Colitis Foundation\nof America.  I do not know if the UK has a similar organization.  The\naddress of\nthe CCFA is \n\nCCFA\n444 Park Avenue South\n11th Floor\nNew York, NY  10016-7374\nUSA\n\nThey have a lot of information available and have a number of newsletters.\n \nGood Luck."

<font color = green >

#### Define custom vectorizer

</font>



In [12]:
three_words_pattern = r"\b\w{3,}\b"
vectorizer = CountVectorizer(
    min_df=20, 
    stop_words='english',
    token_pattern=three_words_pattern) 
vectorizer.fit(newsgroup_data)

CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=20,
        ngram_range=(1, 1), preprocessor=None, stop_words='english',
        strip_accents=None, token_pattern='\\b\\w{3,}\\b', tokenizer=None,
        vocabulary=None)

<font color = green >

#### Review feratures 

</font>



In [13]:
print ('len of features = {:,}\n'.format(len(vectorizer.get_feature_names())))
print (vectorizer.get_feature_names()[:40])


len of features = 902

['000', '100', '1990', '1992', '1993', '200', '2nd', '300', '400', '486', '500', '800', 'ability', 'able', 'accept', 'accepted', 'access', 'according', 'actual', 'actually', 'add', 'addition', 'additional', 'address', 'advance', 'advice', 'age', 'ago', 'agree', 'ahead', 'air', 'allow', 'alt', 'america', 'american', 'answer', 'answers', 'anybody', 'apparently', 'appears']


<font color = green >

#### Vectorize data set

</font>



In [14]:
newsgroup_data_vectorized= vectorizer.transform(newsgroup_data)
print (newsgroup_data_vectorized)

  (0, 23)	1
  (0, 33)	1
  (0, 58)	1
  (0, 76)	1
  (0, 326)	1
  (0, 335)	1
  (0, 386)	1
  (0, 409)	1
  (0, 451)	1
  (0, 456)	1
  (0, 515)	1
  (0, 529)	1
  (0, 545)	1
  (0, 727)	1
  (0, 843)	1
  (0, 900)	1
  (1, 33)	1
  (1, 34)	1
  (1, 84)	1
  (1, 184)	1
  (1, 201)	1
  (1, 214)	1
  (1, 231)	2
  (1, 241)	1
  (1, 324)	1
  :	:
  (1998, 622)	1
  (1998, 625)	3
  (1998, 688)	1
  (1998, 698)	2
  (1998, 726)	1
  (1998, 804)	1
  (1998, 805)	1
  (1998, 810)	10
  (1998, 813)	2
  (1998, 814)	1
  (1998, 816)	1
  (1998, 818)	1
  (1998, 844)	1
  (1998, 882)	2
  (1998, 899)	1
  (1999, 171)	1
  (1999, 194)	1
  (1999, 205)	1
  (1999, 213)	1
  (1999, 276)	2
  (1999, 308)	1
  (1999, 344)	1
  (1999, 669)	1
  (1999, 832)	1
  (1999, 874)	1


<font color = green >

#### Create gensim corpus

</font>



In [15]:
corpus = gensim.matutils.Sparse2Corpus(newsgroup_data_vectorized, documents_columns=False)
# comparing to using corpora.Dictionary:
# corpus = [dictionary.doc2bow(text) for text in texts] 
[item for item in corpus][:5]


[[(23, 1),
  (33, 1),
  (58, 1),
  (76, 1),
  (326, 1),
  (335, 1),
  (386, 1),
  (409, 1),
  (451, 1),
  (456, 1),
  (515, 1),
  (529, 1),
  (545, 1),
  (727, 1),
  (843, 1),
  (900, 1)],
 [(33, 1),
  (34, 1),
  (84, 1),
  (184, 1),
  (201, 1),
  (214, 1),
  (231, 2),
  (241, 1),
  (324, 1),
  (332, 1),
  (359, 1),
  (363, 1),
  (365, 1),
  (409, 1),
  (430, 3),
  (451, 1),
  (475, 1),
  (492, 2),
  (525, 2),
  (605, 1),
  (633, 2),
  (642, 1),
  (674, 1),
  (688, 1),
  (709, 1),
  (750, 1),
  (777, 1),
  (823, 1),
  (838, 1),
  (874, 1),
  (896, 1)],
 [(25, 1),
  (26, 1),
  (63, 1),
  (120, 1),
  (231, 1),
  (297, 1),
  (326, 1),
  (344, 1),
  (373, 1),
  (423, 1),
  (442, 1),
  (444, 1),
  (448, 2),
  (465, 1),
  (572, 1),
  (653, 1),
  (659, 1),
  (714, 1),
  (777, 1),
  (779, 1),
  (781, 1),
  (818, 1),
  (836, 1),
  (855, 1),
  (890, 1),
  (898, 1)],
 [(4, 1),
  (17, 2),
  (18, 1),
  (22, 1),
  (42, 1),
  (48, 2),
  (68, 1),
  (78, 1),
  (86, 1),
  (94, 1),
  (117, 1),
  (119, 1)

<font color = green >

#### Create id2word dictionary

</font>



In [16]:
id_map = dict((v, k) for k, v in vectorizer.vocabulary_.items()) 

<font color = green >

#### Generate LDA model

</font>



In [17]:
ldamodel = gensim.models.ldamodel.LdaModel (corpus, num_topics=6, id2word=id_map, passes=25, random_state=34)
# Comparing to corpora.Dictionary
# ldamodel = gensim.models.ldamodel.LdaModel(corpus, num_topics=2, id2word=dictionary, passes=20, random_state= 0)


<font color = green >

#### Review topics

</font>



In [18]:
ldamodel.print_topics(num_topics=6,num_words=10)

[(0,
  '0.025*"edu" + 0.019*"com" + 0.018*"use" + 0.018*"thanks" + 0.016*"does" + 0.015*"know" + 0.011*"mail" + 0.010*"apple" + 0.009*"help" + 0.008*"want"'),
 (1,
  '0.061*"drive" + 0.039*"disk" + 0.030*"scsi" + 0.027*"drives" + 0.027*"hard" + 0.025*"controller" + 0.021*"card" + 0.018*"rom" + 0.016*"cable" + 0.016*"floppy"'),
 (2,
  '0.024*"people" + 0.022*"god" + 0.012*"atheism" + 0.012*"think" + 0.012*"believe" + 0.012*"don" + 0.010*"does" + 0.010*"just" + 0.009*"argument" + 0.009*"say"'),
 (3,
  '0.023*"game" + 0.021*"year" + 0.020*"team" + 0.013*"games" + 0.013*"play" + 0.011*"good" + 0.011*"don" + 0.010*"think" + 0.010*"season" + 0.010*"players"'),
 (4,
  '0.035*"space" + 0.019*"nasa" + 0.018*"data" + 0.013*"information" + 0.013*"available" + 0.013*"center" + 0.011*"ground" + 0.010*"research" + 0.010*"000" + 0.010*"new"'),
 (5,
  '0.017*"just" + 0.017*"like" + 0.016*"don" + 0.012*"car" + 0.012*"time" + 0.011*"think" + 0.011*"good" + 0.010*"know" + 0.008*"way" + 0.008*"people"')]

<font color = green >

#### Name topics

</font>



In [19]:
topics_names= ['Education', 'Computers & IT', 'Religion', 'Sports', 'Science','Society & Lifestyle']

<font color = green >

#### Classify the new text 

</font>



In [20]:
import numpy as np

In [142]:
new_doc = ["\n\nIt's my understanding that the freezing will start to occur because \
of the\ngrowing distance of Pluto and Charon from the Sun, due to it's\nelliptical orbit. \
It is not due to shadowing effects. \n\n\nPluto can shadow Charon, and vice-versa.\n\nGeorge \
Krumins\n-- "] 


In [143]:
doc_vectorized= vectorizer.transform(new_doc) # input param is list
new_doc_corpus = gensim.matutils.Sparse2Corpus(doc_vectorized, documents_columns=False)
doc_topics = ldamodel.get_document_topics(new_doc_corpus)
list(doc_topics)

[[(0, 0.11149516), (1, 0.8885048)]]

In [144]:
doc_vectorized

<1x902 sparse matrix of type '<class 'numpy.int64'>'
	with 4 stored elements in Compressed Sparse Row format>

In [23]:
def elicit_topic_name(doc_topics):    
    return topics_names[np.squeeze(np.array(doc_topics))[:,1].argmax()]
elicit_topic_name(doc_topics)

'Science'

<font color = green >

## Home Task 

</font>


<font color = green >

### Topic Modeling 

</font>

[voted-kaggle-dataset](https://www.kaggle.com/canggih/voted-kaggle-dataset/version/2#voted-kaggle-dataset.csv)

In [119]:
import nltk
from nltk.tokenize import word_tokenize
from nltk.stem.porter import PorterStemmer
from gensim import corpora, models
from nltk.corpus import stopwords
import pandas as pd
import numpy as np
import gensim
import re

fn=  os.path.join(path , 'voted-kaggle-dataset.csv')
df = pd.read_csv(fn)

In [120]:
df.head(50)

Title  \
0                         Credit Card Fraud Detection   
1                            European Soccer Database   
2                             TMDB 5000 Movie Dataset   
3                           Global Terrorism Database   
4                             Bitcoin Historical Data   
5             Kaggle ML and Data Science Survey, 2017   
6                                        Iris Species   
7                        World Development Indicators   
8              Daily News for Stock Market Prediction   
9                                  Pokemon with stats   
10                             Lending Club Loan Data   
11                                       Wine Reviews   
12     Climate Change: Earth Surface Temperature Data   
13                                    Open Food Facts   
14                    Where it Pays to Attend College   
15                            Mushroom Classification   
16      Breast Cancer Wisconsin (Diagnostic) Data Set   
17                           Amazon Fine Food Reviews   
18                             World Happiness Report   
19                                      Fashion MNIST   
20                                   2016 US Election   
21                                    Game of Thrones   
22                            Speed Dating Experiment   
23                                    Football Events   
24                              Zillow Economics Data   
25                    House Sales in King County, USA   
26                                 The Movies Dataset   
27                            New York Stock Exchange   
28                   Cryptocurrency Historical Prices   
29                                          TED Talks   
30                       Health Insurance Marketplace   
31       (MBTI) Myers-Briggs Personality Type Dataset   
32                          World University Rankings   
33                       Mental Health in Tech Survey   
34                          Huge Stock Market Dataset   
35                       Medical Appointment No Shows   
36                       Twitter US Airline Sentiment   
37                        Gender Recognition by Voice   
38            Every Cryptocurrency Daily Market Price   
39                        Student Alcohol Consumption   
40                      H-1B Visa Petitions 2011-2016   
41                                Young People Survey   
42                  Trending YouTube Video Statistics   
43                                   Video Game Sales   
44                                  20 Years of Games   
45                           Hillary Clinton's Emails   
46  IBM HR Analytics Employee Attrition & Performance   
47                              Chocolate Bar Ratings   
48                      Uber Pickups in New York City   
49                       Getting Real about Fake News   

                                             Subtitle  \
0   Anonymized credit card transactions labeled as...   
1   25k+ matches, players & teams attributes for E...   
2                 Metadata on ~5,000 movies from TMDb   
3   More than 170,000 terrorist attacks worldwide,...   
4   Bitcoin data at 1-min intervals from select ex...   
5   A big picture view of the state of data scienc...   
6   Classify iris plants into three species in thi...   
7   Explore country development indicators from ar...   
8   Using 8 years daily news headlines to predict ...   
9                    721 Pokemon with stats and types   
10                Analyze Lending Club's issued loans   
11  130k wine reviews with variety, location, wine...   
12           Exploring global temperatures since 1750   
13  Explore nutrition facts from foods around the ...   
14    Salaries by college, region, and academic major   
15                      Safe to eat or deadly poison?   
16  Predict whether the cancer is benign or malignant   
17          Analyze ~500,000 food reviews from Amazon   
18  Happiness scored according to economic product...   


In [121]:
print ('len of texts= {:,}'.format(len(df)))
index = 10 
df.loc[index, 'Description']

len of texts= 2,150


'These files contain complete loan data for all loans issued through the 2007-2015, including the current loan status (Current, Late, Fully Paid, etc.) and latest payment information. The file containing loan data through the "present" contains complete loan data for all loans issued through the previous completed calendar quarter. Additional features include credit scores, number of finance inquiries, address including zip codes, and state, and collections among others. The file is a matrix of about 890 thousand observations and 75 variables. A data dictionary is provided in a separate file. k'

In [122]:
df_data_set = df["Description"]
# df["Description"].apply(pd.value_counts) //Note: not working for non numbers type 

In [123]:
en_stop  = set(stopwords.words('english'))
most_frequent = set(['data', 'dataset']);
p_stemmer = PorterStemmer()

def tokenize(df_data_set):
    texts = []
    for doc in df_data_set:
        # tokenize document string
        doc = str(doc)
        raw = doc.lower()
        tokens = word_tokenize(raw)

        # remove stop words from tokens
        tokens = [token for token in tokens if token not in en_stop]
        tokens = [token for token in tokens if token not in most_frequent]

        #remove words that length are less than 3 chars

        tokens =  [token for token in tokens if len(token) >3]
                
        # stem tokens
        tokens = [p_stemmer.stem(token) for token in tokens]

        # add tokens to list
        texts.append(tokens)
      
    return texts

texts = tokenize(df_data_set)
texts[0]

['dataset',
 'contain',
 'transact',
 'made',
 'credit',
 'card',
 'septemb',
 '2013',
 'european',
 'cardhold',
 'present',
 'transact',
 'occur',
 'day',
 'fraud',
 '284,807',
 'transact',
 'highli',
 'unbalanc',
 'posit',
 'class',
 'fraud',
 'account',
 '0.172',
 'transact',
 'contain',
 'numer',
 'input',
 'variabl',
 'result',
 'transform',
 'unfortun',
 'confidenti',
 'issu',
 'provid',
 'origin',
 'featur',
 'background',
 'inform',
 'featur',
 'princip',
 'compon',
 'obtain',
 'featur',
 'transform',
 "'time",
 "'amount",
 'featur',
 "'time",
 'contain',
 'second',
 'elaps',
 'transact',
 'first',
 'transact',
 'featur',
 "'amount",
 'transact',
 'amount',
 'featur',
 'use',
 'example-depend',
 'cost-senst',
 'learn',
 'featur',
 "'class",
 'respons',
 'variabl',
 'take',
 'valu',
 'case',
 'fraud',
 'otherwis',
 'given',
 'class',
 'imbal',
 'ratio',
 'recommend',
 'measur',
 'accuraci',
 'use',
 'area',
 'precision-recal',
 'curv',
 'auprc',
 'confus',
 'matrix',
 'accuraci'

In [124]:
# moby_frequencies = FreqDist(nltk.word_tokenize(texts))


In [125]:
dictionary = corpora.Dictionary(texts) # this is alternative way - without using count vectorizer
print (type(dictionary), dictionary)
for k,w in dictionary.items():
    print (k,w)

<class 'gensim.corpora.dictionary.Dictionary'> Dictionary(32458 unique tokens: ["'amount", "'class", "'time", '//mlg.ulb.ac.b', '//mlg.ulb.ac.be/artml']...)
0 'amount
1 'class
2 'time
3 //mlg.ulb.ac.b
4 //mlg.ulb.ac.be/artml
5 //mlg.ulb.ac.be/bruf
6 0.172
7 2013
8 2015
9 284,807
10 account
11 accuraci
12 amount
13 analys
14 andrea
15 area
16 auprc
17 avail
18 background
19 bontempi
20 bruxel
21 caelen
22 calibr
23 card
24 cardhold
25 case
26 cidm
27 cite
28 class
29 classif
30 collabor
31 collect
32 compon
33 comput
34 confidenti
35 confus
36 contain
37 cost-senst
38 credit
39 current
40 curv
41 dataset
42 day
43 detail
44 detect
45 elaps
46 european
47 example-depend
48 featur
49 first
50 fraud
51 gianluca
52 given
53 group
54 highli
55 http
56 ieee
57 imbal
58 inform
59 input
60 intellig
61 issu
62 johnson
63 learn
64 libr
65 machin
66 made
67 matrix
68 meaning
69 measur
70 mine
71 numer
72 obtain
73 occur
74 olivi
75 origin
76 otherwis
77 past
78 pleas
79 posit
80 pozzolo
81 precisi

786 conduct
787 convers
788 conversionrates.csv
789 correspond
790 cut
791 day-to-day
792 decod
793 describ
794 edg
795 email
796 employ
797 establish
798 exclud
799 flag
800 folk
801 form
802 free
803 freeform
804 freeformresponses.csv
805 happen
806 ident
807 industry-wid
808 initi
809 interact
810 kind
811 less
812 live
813 median
814 month
815 multipl
816 multiplechoiceresponses.csv
817 non-random
818 novemb
819 open-end
820 option
821 packag
822 primarili
823 proceed
824 protect
825 pud
826 quantmod
827 rank
828 read
829 receiv
830 regard
831 relev
832 respond
833 respondenttypereadme.txt
834 salari
835 schema.csv
836 scientist
837 segment
838 shown
839 singl
840 spam
841 survey
842 survey-tak
843 territori
844 total
845 usabl
846 week
847 window
848 write
849 1936
850 classic
851 fisher
852 flower
853 iri
854 linearli
855 paper
856 petallengthcm
857 petalwidthcm
858 problem
859 r.a.
860 repositori
861 sampl
862 sepallengthcm
863 sepalwidthcm
864 speci
865 taxonom
866 along
867 an

1477 favor
1478 fourth
1479 freedom
1480 gain
1481 gallup
1482 generos
1483 higher
1484 highest
1485 imaginari
1486 incom
1487 increasingli
1488 ladder
1489 landmark
1490 larg
1491 least
1492 least-happi
1493 level
1494 main
1495 march
1496 occasion
1497 over-
1498 policy-mak
1499 poll
1500 poorli
1501 psycholog
1502 quit
1503 recognit
1504 residu
1505 seen
1506 smaller
1507 sub-bar
1508 succeed
1509 support
1510 therefor
1511 third
1512 today
1513 un-reli
1514 under-explain
1515 unexplain
1516 unpleas
1517 utopia
1518 well-b
1519 whole
1520 width
1521 //github.com/zalandoresearch/fashion-mnist
1522 //pjreddie.com/projects/mnist-in-csv/
1523 //tech.zalando.com
1524 10,000
1525 255.
1526 28x28
1527 60,000
1528 ai/ml/data
1529 and/or
1530 ankl
1531 aris
1532 ascii-diagram
1533 assign
1534 boot
1535 charg
1536 claim
1537 cloth
1538 coat
1539 commun
1540 connect
1541 convert
1542 copi
1543 copyright
1544 dark
1545 darker
1546 decompos
1547 direct
1548 dress
1549 drop-in
1550 fail
1551 fash

2785 satisfactori
2786 solid
2787 storag
2788 straight
2789 summar
2790 superior
2791 terroir
2792 transcend
2793 unpalat
2794 vision
2795 14.3
2796 2014.
2797 affiliated_base_num
2798 american_b01362.csv
2799 b02512
2800 b02598
2801 b02617
2802 b02682
2803 b02764
2804 b02765
2805 b02835
2806 b02836
2807 borough
2808 carmel_b00256.csv
2809 coarse-grain
2810 commiss
2811 danach-ni
2812 date/tim
2813 dial7_b00887.csv
2814 diplo_b01196.csv
2815 dispatch
2816 dispatching_base_num
2817 dreist
2818 drinnen
2819 driver
2820 essenti
2821 federal_02216.csv
2822 fine-grain
2823 firstclass_b01536.csv
2824 fivethirtyeight
2825 foil
2826 for-hir
2827 grun
2828 highclass_b01717.csv
2829 hinter
2830 januari
2831 latitud
2832 limousin
2833 locationid
2834 longitud
2835 lyft_b02510.csv
2836 non-ub
2837 other-fhv-data-jan-aug-2015.csv
2838 outer
2839 pickup
2840 pickup_d
2841 prestige_b01338.csv
2842 ride
2843 rush-hour
2844 schmecken
2845 sept.
2846 skyline_b00111.csv
2847 taxi
2848 taxi-zone-lookup.cs

3535 clubpictures.zip
3536 compress
3537 doubl
3538 emblem
3539 fanat
3540 fastest/slowest
3541 fifaindex.com
3542 fulldata.csv
3543 globe
3544 interchang
3545 liter
3546 logo
3547 organis
3548 outfield
3549 pick
3550 pictures.zip
3551 pictures_f.zip
3552 playernames.csv
3553 playground..
3554 pressur
3555 proxi
3556 realis
3557 reli
3558 scout
3559 stamina
3560 tough
3561 uniform
3562 url
3563 young
3564 youngster
3565 .txt
3566 //archive.org/download/nf_prize_dataset.tar
3567 //netflixprize.com/index.html
3568 //www.netflixprize.com/faq
3569 1,000,000
3570 1,2,3,4
3571 1234,2005-05-26
3572 17770
3573 1890
3574 19th
3575 23rd
3576 2649429
3577 3245
3578 3245,2005-12-19
3579 3456,2005-11-07
3580 480189
3581 5666
3582 5666,2005-12-23
3583 6789,2005-03-14
3584 bellkor
3585 chao
3586 cinematch
3587 colon
3588 combined_data_
3589 customerid
3590 customerid11
3591 customerid12
3592 customerid21
3593 customerid22
3594 date11
3595 date12
3596 date21
3597 date22
3598 decemeb
3599 empti
3600 ga

...

28777 sasikumar
28778 saswata
28779 satadru5
28780 satavisha
28781 satheeshperepu
28782 sathu79
28783 sathyajit
28784 satish
28785 satya
28786 satyaki
28787 satyasai
28788 saudal-zakwani
28789 saurabh
28790 saurabhbhagvatula
28791 saurav
28792 sauro
28793 savannahlogan
28794 savasyä±ldä±rä±m
28795 savchenko
28796 savioz
28797 sawayaka
28798 saxena
28799 saxin
28800 sazidurrahman
28801 schale
28802 scharf
28803 schenck
28804 schiller
28805 schirmer
28806 schmidt
28807 schnessl
28808 schreier
28809 schroeder
28810 schwartz
28811 schwertfeg
28812 scottfre
28813 scotthendrickson
28814 seagoat
28815 seagullbird
28816 seankim
28817 seanlahman
28818 sebastian
28819 sebastianmarkow
28820 sebastianzanabria
28821 sebel
28822 secareanu
28823 security3test
28824 securityteamvictim4
28825 seetharam
28826 sehgal
28827 seibert
28828 seiei
28829 sekar
28830 sekhar
28831 sekkaf
28832 selah
28833 selvakumar
28834 semenyk
28835 semin
28836 semionkorchevskiy
28837 seong-ja
28838 seregni
28839 serena
28840

29526 xaliap
29527 xavierbay
29528 xaviermartinezbartra
29529 xavya
29530 xgan
29531 xiao
29532 xiaocongsonia
29533 xiaojingli
29534 xiaotong
29535 xiaoxiao
29536 xiaozhou
29537 xime
29538 xingzhangren
29539 xiong
29540 xjtushilei
29541 xss'
29542 xtyscut
29543 xuan
29544 xuetao
29545 xuleiyang
29546 xuseniayu
29547 xuy2
29548 xwang
29549 yabir
29550 yachuncheng
29551 yadav
29552 yagana
29553 yagnesh
29554 yahyacivelek
29555 yalitsai
29556 yamaji
29557 yamuuu
29558 yanir
29559 yanni
29560 yannmallegol
29561 yannsar
29562 yaohsiao
29563 yaoseny
29564 yaoxiang
29565 yapi
29566 yarden
29567 yasar
29568 yash
29569 yashjain
29570 yashna
29571 yashu
29572 yasmeenw
29573 yassin
29574 yassineameur
29575 yasuhiro_121
29576 yaswanth
29577 yatishbn
29578 yazi
29579 yeomyungro
29580 yeongchan
29581 yeongseok
29582 yetukuri
29583 yevgeniya
29584 yexiaofeng
29585 yichenâ€œeddieâ€shen
29586 yifan
29587 yijiezhuang
29588 yilmaz
29589 yime
29590 ying
29591 yinghan
29592 yingzhu
29593 yiqizhang
29594 y

30276 tulpenwoed
30277 tulpomani
30278 well.
30279 上证综合指数前复权日线数据
30280 'decad
30281 'mysteri
30282 //www.fisheaters.com/rosary.html
30283 //www.preces-latinae.org/thesaurus/bvm/rosarium.html
30284 dominican
30285 joy
30286 novic
30287 pray
30288 prayer
30289 rosari
30290 sorrow
30291 disburs
30292 extet
30293 feaf
30294 sorti
30295 squadron
30296 broadsid
30297 eighteenth
30298 fugit
30299 pamphlet
30300 autobiographi
30301 egalitarian
30302 evangel
30303 metaphor
30304 post-revolutionari
30305 renov
30306 errant
30307 for-excel
30308 doha
30309 //data.betfair.com/sportids.htm
30310 //www.kaggle.com/zygmunt/betfair-hors
30311 104049
30312 1306731
30313 1477
30314 2152880
30315 26420387
30316 3503
30317 3988
30318 4339
30319 468328
30320 61420
30321 6231
30322 6422
30323 6423
30324 7511
30325 7522
30326 7524
30327 998917
30328 gaelic
30329 greyhound
30330 handbal
30331 rugbi
30332 snooker
30333 volleybal
30334 //archive.spectator.co.uk/article/24th-september-2005/57/doctor-in-the-hous
3

31026 article-id
31027 article-titl
31028 beta-1
31029 bioavail
31030 bsa/pbst
31031 cane
31032 cluster_id
31033 cripto
31034 cytokin
31035 de-orphan
31036 degf
31037 diod
31038 elisa
31039 eno
31040 enzym
31041 evolutionarili
31042 extracellular
31043 g-protein
31044 gnb3
31045 il-17
31046 journal-titl
31047 l-shape
31048 luciferas
31049 lxml
31050 meta-analysi
31051 mg/ml
31052 monoclon
31053 mutant
31054 ncbi
31055 ncbi_data.json
31056 ncbi_doc_titles_map.json
31057 ncbi_lines_map.json
31058 non-fit
31059 non-specif
31060 phenix.refin
31061 pias3
31062 plagiar
31063 polymorph
31064 pymol
31065 rmsd
31066 solubl
31067 supernat
31068 tgf-
31069 tgf-b
31070 tgfb1
31071 therapeut
31072 tumorigen
31073 tyro3
31074 tyrosin
31075 uspto_data.json
31076 uspto_doc_titles_map.json
31077 uspto_lines_map.json
31078 well-character
31079 xpath
31080 card_detail.csv
31081 corner_detail.csv
31082 cross_detail.csv
31083 datadictionary.xlsx
31084 foulcommit
31085 foulcommit_detail.csv
31086 goal_detai

31776 employee_agreements.csv
31777 income_sources_and_assets.csv
31778 jobs_before_joining_admin.csv
31779 names_and_job_titles.csv
31780 billi
31781 depodesta
31782 hillsid
31783 on-bas
31784 oobp
31785 oslg
31786 rankplayoff
31787 rankseason
31788 sports-reference.com
31789 unsettl
31790 1.25kg
31791 20-28
31792 bicep
31793 curl
31794 dumbbel
31795 elbow
31796 hip
31797 puc-rio
31798 unilater
31799 wearer
31800 weight-loss
31801 wugulino
31802 'surrog
31803 0.95
31804 1.05
31805 dbot
31806 econc
31807 esoil
31808 gammag
31809 mr_c
31810 mr_t
31811 mt_c
31812 mt_t
31813 parametr
31814 predicted_valu
31815 self-mad
31816 true_valu
31817 //www.asx.com.au/
31818 //www.asxhistoricaldata.com/
31819 1997-01-02
31820 2,228
31821 6,475,470
31822 asx-equity-price.csv
31823 asx-tickers.csv
31824 gaint
31825 at_confer
31826 livetweet
31827 lower-ti
31828 modern-world
31829 //www1.nyc.gov/site/planning/data-maps/open-data/districts-download-metadata.pag
31830 openphish.com
31831 phish
31832 dhh


In [126]:
print ('\nconvert tokenized documents into a document-term matrix')
corpus = [dictionary.doc2bow(text) for text in texts] # id and count
for item in corpus:
    print (item)


convert tokenized documents into a document-term matrix
[(0, 2), (1, 1), (2, 2), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 2), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 2), (29, 2), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 3), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 7), (49, 1), (50, 4), (51, 1), (52, 1), (53, 1), (54, 1), (55, 3), (56, 1), (57, 1), (58, 1), (59, 1), (60, 1), (61, 1), (62, 1), (63, 2), (64, 1), (65, 1), (66, 1), (67, 1), (68, 1), (69, 1), (70, 2), (71, 1), (72, 1), (73, 1), (74, 1), (75, 1), (76, 1), (77, 1), (78, 1), (79, 1), (80, 1), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 1), (94, 1), (95, 1), (96, 1), (97, 1), (98, 1), (99, 7), (100, 2), (101, 3), (102, 1), (103, 1), (104, 1), (1

[(138, 1), (189, 1), (199, 2), (206, 2), (257, 1), (670, 1), (675, 1), (1726, 1), (1783, 1), (5252, 1), (5253, 1), (5254, 1), (5255, 1), (5256, 1), (5257, 1)]
[(36, 1), (41, 1), (52, 1), (55, 1), (121, 1), (139, 1), (142, 2), (164, 2), (172, 2), (186, 1), (189, 1), (194, 1), (204, 1), (223, 1), (245, 2), (255, 2), (267, 1), (270, 1), (275, 1), (296, 1), (314, 1), (325, 1), (337, 1), (348, 2), (351, 1), (359, 1), (365, 1), (375, 1), (376, 1), (383, 7), (399, 1), (423, 1), (430, 1), (461, 1), (475, 2), (500, 1), (501, 1), (530, 1), (533, 1), (606, 1), (632, 1), (655, 1), (711, 1), (718, 1), (743, 1), (756, 1), (767, 1), (802, 1), (815, 1), (846, 2), (892, 2), (903, 6), (914, 1), (933, 2), (962, 1), (964, 1), (1106, 2), (1261, 1), (1423, 1), (1604, 1), (1634, 1), (1670, 1), (1720, 1), (1776, 1), (2113, 1), (2262, 1), (2281, 1), (3033, 1), (3166, 2), (3446, 1), (3543, 1), (3872, 1), (3883, 1), (4139, 1), (4221, 1), (4230, 2), (4737, 1), (5258, 1), (5259, 1), (5260, 1), (5261, 1), (5262, 1)

[(31, 1), (195, 1), (362, 1), (2124, 1)]
[(7, 1), (8, 3), (13, 1), (58, 4), (77, 1), (78, 1), (86, 1), (91, 1), (98, 1), (105, 3), (125, 1), (141, 1), (158, 1), (166, 1), (180, 2), (184, 1), (187, 1), (195, 3), (197, 1), (204, 1), (211, 1), (212, 1), (222, 1), (223, 2), (228, 1), (255, 1), (270, 2), (274, 1), (275, 1), (288, 1), (290, 1), (301, 1), (328, 1), (335, 1), (343, 2), (346, 1), (359, 1), (424, 1), (430, 2), (452, 1), (471, 1), (480, 1), (500, 1), (501, 1), (512, 1), (513, 1), (518, 1), (534, 1), (542, 1), (546, 1), (547, 1), (598, 1), (606, 1), (611, 2), (615, 1), (617, 2), (623, 1), (639, 1), (647, 1), (673, 1), (730, 1), (736, 2), (743, 2), (749, 1), (769, 3), (832, 1), (841, 5), (861, 1), (933, 1), (954, 1), (975, 2), (997, 2), (1015, 1), (1051, 1), (1312, 1), (1333, 2), (1343, 3), (1399, 1), (1458, 1), (1509, 1), (1539, 4), (1658, 1), (1667, 2), (1779, 1), (1802, 1), (1842, 1), (1867, 1), (1879, 1), (1938, 1), (2019, 1), (2053, 1), (2135, 1), (2170, 1), (2184, 1), (2267, 

[(12, 2), (36, 3), (42, 1), (55, 1), (82, 1), (98, 2), (139, 1), (149, 1), (157, 1), (176, 1), (193, 2), (197, 2), (201, 1), (210, 1), (223, 1), (227, 2), (241, 1), (258, 1), (274, 1), (275, 1), (337, 1), (343, 1), (349, 2), (359, 1), (372, 1), (383, 1), (395, 2), (448, 2), (453, 4), (492, 1), (500, 1), (501, 1), (517, 2), (563, 1), (595, 1), (660, 5), (661, 1), (682, 1), (686, 1), (718, 2), (730, 3), (738, 1), (741, 3), (760, 2), (767, 1), (901, 1), (923, 5), (932, 1), (933, 1), (981, 1), (982, 1), (1032, 5), (1055, 1), (1493, 2), (1599, 2), (1732, 1), (1815, 4), (1840, 1), (1862, 2), (1911, 1), (2044, 1), (2064, 1), (2106, 1), (2124, 1), (2601, 1), (2615, 1), (3316, 2), (3407, 2), (3773, 2), (6365, 1), (9330, 1), (15210, 2), (20499, 1), (20500, 1), (20501, 1), (20502, 1), (20503, 3), (20504, 1), (20505, 1), (20506, 1), (20507, 1)]
[(36, 1), (58, 1), (258, 1), (741, 1), (1140, 1), (1152, 1), (7476, 1), (20508, 1)]
[(8, 1), (12, 1), (25, 3), (28, 1), (36, 1), (41, 1), (42, 1), (52, 1),

[(895, 1)]
[(895, 1)]
[(31, 3), (55, 2), (78, 1), (85, 3), (149, 1), (169, 2), (172, 1), (175, 1), (180, 1), (241, 1), (255, 1), (267, 1), (275, 1), (346, 3), (359, 1), (423, 1), (495, 1), (500, 1), (501, 1), (580, 1), (659, 2), (706, 1), (713, 1), (736, 1), (751, 1), (955, 3), (982, 2), (1058, 1), (1106, 1), (1333, 1), (1399, 4), (1550, 1), (1582, 1), (2026, 1), (2050, 1), (2220, 1), (2955, 1), (3916, 1), (5287, 1), (5387, 1), (10996, 1), (25499, 1), (25500, 1), (25501, 1)]
[(55, 2), (63, 1), (99, 2), (100, 1), (232, 2), (275, 1), (359, 2), (401, 1), (478, 1), (500, 1), (501, 1), (892, 1), (925, 1), (1368, 1), (2248, 1), (2278, 2), (2625, 2), (25502, 1), (25503, 1)]
[(17, 2), (36, 1), (41, 1), (98, 1), (105, 1), (106, 2), (125, 1), (132, 1), (142, 1), (143, 1), (180, 1), (181, 1), (189, 2), (205, 1), (210, 1), (221, 1), (238, 1), (246, 1), (261, 2), (270, 1), (337, 2), (360, 1), (389, 4), (466, 1), (533, 1), (649, 1), (666, 1), (694, 3), (700, 2), (709, 1), (718, 1), (730, 1), (736, 1

[(895, 1)]
[(895, 1)]
[(895, 1)]
[(231, 2), (267, 1), (275, 1), (337, 3), (346, 2), (359, 1), (500, 1), (501, 1), (802, 1), (871, 1), (2608, 2), (4073, 2), (7768, 1)]
[(895, 1)]
[(28, 1), (31, 1), (71, 1), (105, 1), (124, 1), (129, 2), (189, 1), (201, 1), (222, 2), (244, 1), (245, 1), (372, 1), (374, 2), (380, 1), (384, 1), (420, 2), (424, 1), (489, 5), (507, 1), (623, 1), (708, 1), (858, 3), (886, 1), (981, 1), (1003, 1), (1015, 1), (1036, 1), (1062, 1), (1121, 1), (1276, 1), (1305, 11), (1490, 2), (1506, 1), (1529, 1), (1660, 1), (1730, 7), (1782, 1), (1921, 1), (2024, 1), (2085, 1), (2188, 1), (2189, 1), (2968, 1), (3018, 1), (3028, 1), (3118, 1), (3270, 1), (3505, 7), (3650, 1), (3972, 1), (4476, 2), (4477, 2), (4478, 1), (4479, 1), (4480, 3), (4481, 1), (4482, 1), (4483, 1), (4484, 1), (4485, 1), (4486, 1), (4487, 1), (4488, 3), (4489, 1), (4490, 1), (4491, 1), (4492, 1), (4493, 1), (4494, 4), (4495, 1), (4496, 3), (4497, 1), (4498, 1), (4499, 1), (4500, 1), (4501, 1), (4502, 1), 

In [107]:
ldamodel = gensim.models.ldamodel.LdaModel(
    corpus, num_topics=2, id2word=dictionary, passes=20, random_state= 0)

In [109]:
ldamodel.print_topics(num_topics=5,num_words=15)

[(0,
  '0.047*"univers" + 0.010*"state" + 0.006*"descript" + 0.006*"use" + 0.006*"colleg" + 0.006*"model" + 0.005*"contain" + 0.005*"featur" + 0.005*"column" + 0.005*"imag" + 0.004*"http" + 0.004*"learn" + 0.004*"context" + 0.004*"time" + 0.003*"california"'),
 (1,
  '0.007*"content" + 0.007*"use" + 0.006*"contain" + 0.006*"acknowledg" + 0.006*"context" + 0.006*"time" + 0.006*"file" + 0.005*"inform" + 0.005*"includ" + 0.005*"inspir" + 0.005*"number" + 0.004*"year" + 0.004*"http" + 0.004*"name" + 0.003*"collect"')]

In [148]:
topics_names= ['Education', 'Communication']

In [151]:
corpus

[[(0, 2),
  (1, 1),
  (2, 2),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 1),
  (8, 1),
  (9, 1),
  (10, 1),
  (11, 2),
  (12, 1),
  (13, 1),
  (14, 1),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 1),
  (20, 1),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 1),
  (27, 1),
  (28, 2),
  (29, 2),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 1),
  (34, 1),
  (35, 1),
  (36, 3),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 1),
  (41, 1),
  (42, 1),
  (43, 1),
  (44, 1),
  (45, 1),
  (46, 1),
  (47, 1),
  (48, 7),
  (49, 1),
  (50, 4),
  (51, 1),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 3),
  (56, 1),
  (57, 1),
  (58, 1),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 2),
  (64, 1),
  (65, 1),
  (66, 1),
  (67, 1),
  (68, 1),
  (69, 1),
  (70, 2),
  (71, 1),
  (72, 1),
  (73, 1),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 1),
  (78, 1),
  (79, 1),
  (80, 1),
  (81, 1),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 1),
  (86, 1),
  (87, 1),
  (88, 1),
  (89, 1),
  (90, 1),
  (91, 1)

In [152]:
def elicit_topic_name(doc_topics):    
    return topics_names[np.squeeze(np.array(doc_topics))[:,1].argmax()]
elicit_topic_name(doc_topics)

IndexError: too many indices for array

<font color = green >

## Learn more
</font>

Latent Dirichlet allocation
<br>
https://en.wikipedia.org/wiki/Latent_Dirichlet_allocation


<font color = green >

## Next lesson: Clustering 
</font>

